In [1]:
import sqlite3

import pandas as pd

from sklearn.feature_extraction.text import CountVectorizer

# CONFIG
DB_PATH = '1_after_cleaning_databases/1000_devices_media_cleaned.db'
TABLE_NAME = 'css_attribute'
OUTPUT_NAME = 'feature_matrix_media'

## PANDAS
pd.set_option('future.no_silent_downcasting', True)
# Set pandas options to display the full DataFrame
pd.set_option('display.max_rows', None)  # Show all rows
pd.set_option('display.max_columns', None)  # Show all columns
pd.set_option('display.width', None)  # Disable line wrapping
pd.set_option('display.max_colwidth', None)  # Show full content in each column
pd.set_option('display.max_seq_item', 100000)  # Show all items in a sequence (e.g., lists, dictionaries)

# Optionally, increase the display buffer size
pd.set_option('display.max_info_columns', 100000)  # Show all columns in df.info()

# If you have very large dataframes, increasing this might help
pd.set_option('display.max_rows', 1000)  # You can change 1000 to a higher value if needed

### Functions

#### Loading data from sqlite to pandas dataframe

In [2]:
def load_sqlite_to_dataframe(db_path, table_name):
    conn = sqlite3.connect(db_path)
    df = pd.read_sql(f"SELECT * FROM {table_name}", conn)
    conn.close()
    return df

#### Changing boolean values to 1 and 0

In [3]:
def convert_booleans(value):
    true_values = {'enabled'}
    false_values = {'disabled'}

    if isinstance(value, str):
        val_lower = value.lower()
        if val_lower in true_values:
            return 1
        elif val_lower in false_values:
            return 0
    return value

#### Constructing feature matrix

In [4]:
def create_feature_matrix(df):
    # Handle fonts
    fonts = (
        df[df['attribute'] == 'font']
        .groupby('session_id')['value']
        .apply(lambda x: ';'.join(sorted(set(x))))
        .reset_index()
    )

    # replace spaces in font names with underscores
    fonts['value'] = fonts['value'].str.replace(' ', '_', regex=False)

    # Rest of features
    non_fonts = df[df['attribute'] != 'font'].copy()
    non_fonts['feature_name'] = non_fonts['source'] + ':' + non_fonts['attribute']

    # Apply boolean conversion
    non_fonts['value'] = non_fonts['value'].apply(convert_booleans)

    # Pivot table
    pivot = non_fonts.pivot_table(index='session_id',
                                  columns='feature_name',
                                  values='value',
                                  aggfunc='first').reset_index()

    # Merge fonts back
    full_df = pivot.merge(fonts, on='session_id', how='left')

    full_df.rename(columns={'value': 'fonts'}, inplace=True)

    return full_df

#### Changing font values to one-hot encoding

In [5]:
def vectorize_fonts(df, font_column='fonts'):
    vectorizer = CountVectorizer(tokenizer=lambda x: [token.strip() for token in x.split(';') if token.strip()])
    font_features = vectorizer.fit_transform(df[font_column].fillna(''))

    font_df = pd.DataFrame(
        font_features.toarray(),
        columns=[f'css:font_{f}' for f in vectorizer.get_feature_names_out()],
        index=df.index
    )

    font_df['css:font_vector'] = font_df.astype(str).agg(''.join, axis=1)

    df = df.drop(columns=[font_column]).join(font_df)
    return df

#### Cleaning feature types

In [6]:
def clean_feature_types(df):
    for col in df.columns:
        # todo bedzie trzeba na to spojrzec gdy dojda kolejne atrybuty bo jest to takie niezbyt uniwersalne
        if col.startswith('css:env') or col.startswith("css:media") or col.startswith('js:env') or 'width' in col or 'height' in col:
            df[col] = pd.to_numeric(df[col], errors='coerce')

    # Fill missing numeric with -1
    numeric_cols = df.select_dtypes(include='number').columns
    df[numeric_cols] = df[numeric_cols].fillna(-1)

    # Fill missing non-numeric with empty string
    object_cols = df.select_dtypes(include='object').columns
    df[object_cols] = df[object_cols].fillna('')

    df = df.infer_objects()

    return df

#### Save datagframe to parquet

In [7]:
def save_features(df):
    df.to_parquet(f'2_after_feature_extraction/{OUTPUT_NAME}.parquet')
    df.to_csv(f'2_after_feature_extraction/{OUTPUT_NAME}.csv', index=False)

### Execution

In [8]:
# Load data
df_raw = load_sqlite_to_dataframe(DB_PATH, TABLE_NAME)

In [9]:
# Create feature matrix
df_features = create_feature_matrix(df_raw)

In [10]:
df_features

session_id browserstack:browser  \
0    002fc90c-b5a1-4db9-a469-3e31ef506b36                 edge   
1    00964d52-4547-49f6-8161-42c9f5b85fb6              firefox   
2    00ca66db-dcc8-4e63-a1ec-358c641e5d62                 edge   
3    00dbd708-2007-45ee-affe-44af226d935f       chrome_android   
4    00e9af93-70c0-4a67-b38d-41e488a63f15       chrome_android   
5    00fdffc9-f32f-4143-8eb5-c86c5da72a25                 edge   
6    012d4223-904f-4375-a9b0-1f0237c05b03                 edge   
7    01334116-382c-4bc3-8662-9d4fe217d955              firefox   
8    017a63c7-7321-45c0-83f1-53dba5ea049c              firefox   
9    017d09c4-da05-44c2-90f2-ffdf0133dea8                 edge   
10   01a533c9-8a95-43d6-a98c-0a4cea838315                 edge   
11   02303702-6d90-4b36-9673-b06cc21b59ff              firefox   
12   026a978d-a5db-4490-86f4-9768ecb05f36       chrome_android   
13   0270acd3-599f-4260-9525-360b819c8581               chrome   
14   02aa5cdd-bf67-4b59-acb6-510c9d69de71              samsung   
15   02b26996-9c57-45ae-9b03-1d158ce3908f              samsung   
16   03d608fb-4df7-471f-b124-a2c7b2db85eb                 edge   
17   04ba4372-e66e-43ea-9bd6-9309337758a4               chrome   
18   04c25ada-4986-4337-822c-6ca95a1d35c0              firefox   
19   050117ff-a078-430e-9826-303bdca6d022              firefox   
20   05723c55-8c60-40cc-8541-103d7dc510dc      chromium_iphone   
21   05ed8036-1337-41c4-925e-ea319b54ac6f               chrome   
22   05f75f51-b884-4b51-9cb8-22094fa7c4b2                 edge   
23   0629363f-dfe2-46c7-bf59-ade07ac2c3f3                 edge   
24   06641def-0189-4f6b-a101-2aa8460c2552                 edge   
25   069eb583-1070-43f8-9e4e-312aa91adeb6       chrome_android   
26   06b1dbd7-58af-4e33-b971-bc07123f36b1              firefox   
27   06bfcb0b-537f-4741-8e35-08e31e9f471f              firefox   
28   07c21b3b-79a6-47dd-a74b-acb6b43a6035                 edge   
29   08234179-98a2-4ab3-8f87-eabfef96c03d               iphone   
30   0848ab96-a8f8-4cae-b4dd-ec5793f24be1              firefox   
31   0851a14c-d87b-4799-a1f0-ff19cac25d25              firefox   
32   08778ad2-04cd-44c8-9e10-64ec3156de7f              firefox   
33   08962923-f91d-4d3e-be49-19e893e0ad54                 edge   
34   09307a20-eb7c-4c32-910a-3879bd4266d7              samsung   
35   094d93e9-c08b-4034-8e9d-c360167687ae                 edge   
36   098b75d2-3166-44bf-a147-ec5ae6d9541a               chrome   
37   09b8ed71-6b4b-40b3-8bb8-c296a84f4bf6              samsung   
38   09dfc229-dd65-4934-a50a-aac9955a0098              samsung   
39   0a0562e4-8ace-4f68-b583-5f96405150b9               chrome   
40   0a32aa8b-f23e-4e04-b29b-f4ca1653b5c9        chromium_ipad   
41   0a4d6a94-64bf-4df3-acae-791ff3db522f                 edge   
42   0a7a6e78-6cdc-4ca1-91c8-d65aed558ce8       chrome_android   
43   0a80f532-afbb-40a2-ac3a-e911b5094277               chrome   
44   0ad78aa6-9745-45e2-85dd-9fb2312e148c               chrome   
45   0affbec7-676a-455b-8efa-bcd5f8bab191              firefox   
46   0b410033-0f39-46b6-bcec-396441ef5781              firefox   
47   0baf65f6-c3fa-406e-9a75-f0a229c38e23              firefox   
48   0bd6e52f-cb96-48ca-8863-47da2e2bdbff       chrome_android   
49   0c3f0868-fa2e-4104-be79-61cc9bfa92d5              firefox   
50   0c70e5be-13e1-4de5-b765-c2cddae8d4d9              firefox   
51   0d30b4a9-a11a-4be1-b688-a26f4e58962e               chrome   
52   0d47117e-c98d-4416-99c9-b3eec897a772              firefox   
53   0d57fb7d-46ab-477b-b51a-11671313a45d       chrome_android   
54   0d78728d-d4b4-4833-8fe1-f81497e18f4c                 edge   
55   0dd46172-7b6e-43ad-ab78-70f98c848809               chrome   
56   0e331f7c-20f8-44e2-be2a-2dfa0b6e4967              firefox   
57   0e982e87-044a-4f54-b59e-d163e42c2ada               chrome   
58   0ea808c0-e919-4676-bf7c-6086b5f30251              firefox   
59   0f40d23e-2e4b-4b81-8605-9f48a3f57cbd               chrome   
60   

In [11]:
# Vectorize fonts
df_features = vectorize_fonts(df_features)

C:\Programs\TBO\tbo-task1\Python\Flask_Book_Library\.venv\Lib\site-packages\sklearn\feature_extraction\text.py:517: UserWarning: The parameter 'token_pattern' will not be used since 'tokenizer' is not None'
  warnings.warn(


In [12]:
# Clean feature types
df_ready = clean_feature_types(df_features)

In [13]:
# test Output
print(f"Shape of feature matrix: {df_ready.shape}")
display(df_ready.head())

Shape of feature matrix: (918, 95)


session_id browserstack:browser  \
0  002fc90c-b5a1-4db9-a469-3e31ef506b36                 edge   
1  00964d52-4547-49f6-8161-42c9f5b85fb6              firefox   
2  00ca66db-dcc8-4e63-a1ec-358c641e5d62                 edge   
3  00dbd708-2007-45ee-affe-44af226d935f       chrome_android   
4  00e9af93-70c0-4a67-b38d-41e488a63f15       chrome_android   

  browserstack:browser_version browserstack:os browserstack:os_version  \
0                        105.0            OS X                 Big Sur   
1                        122.0            OS X                Monterey   
2                        124.0            OS X                 Ventura   
3                      unknown         android                    10.0   
4                      unknown         android                    11.0   

   browserstack:real_height  browserstack:real_width  \
0                      1011                     1200   
1                       949                     1280   
2                      1011                     1200   
3                       727                      393   
4                      1037                      753   

                                                                                                                            css:User-Agent  \
0  Mozilla/5.0 (Macintosh; Intel Mac OS X 10_15_7) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/105.0.0.0 Safari/537.36 Edg/105.0.1343.25   
1                                                     Mozilla/5.0 (Macintosh; Intel Mac OS X 10.15; rv:122.0) Gecko/20100101 Firefox/122.0   
2      Mozilla/5.0 (Macintosh; Intel Mac OS X 10_15_7) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/124.0.0.0 Safari/537.36 Edg/124.0.0.0   
3                          Mozilla/5.0 (Linux; Android 10; K) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/128.0.0.0 Mobile Safari/537.36   
4                                 Mozilla/5.0 (Linux; Android 10; K) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/133.0.0.0 Safari/537.36   

  css:browser  css:env-1-height  css:env-1-width  css:env-10-height  \
0      chrome               136              195                166   
1     firefox               124              196                309   
2      chrome               136              195                166   
3      chrome               130              224                169   
4      chrome               130              224                168   

   css:env-10-width  css:env-11-height  css:env-11-width  css:env-12-height  \
0               711                175              1100                123   
1               470                164              1100                116   
2               712                175              1100                123   
3               785                167              1100                121   
4               784                167              1100                120   

   css:env-12-width  css:env-13-height  css:env-13-width  css:env-14-height  \
0              6762                125                84                130   
1              6973                124                74                130   
2              6762                125                84                130   
3              6866                126                85                131   
4              7125                126                90                130   

   css:env-14-width  css:env-2-height  css:env-2-width  css:env-3-height  \
0                78               188              403               110   
1                74               180              400               104   
2                78               188              403               110   
3                76               163              454               105   
4                77               182              468               105   

   css:env-3-width  css:env-5-height  css:env-5-width  css:env-6-height  \
0              133               100              600               164   
1              133       

In [14]:
save_features(df_ready)

In [15]:
# list all columns
print(df_ready.columns)

Index(['session_id', 'browserstack:browser', 'browserstack:browser_version',
       'browserstack:os', 'browserstack:os_version',
       'browserstack:real_height', 'browserstack:real_width', 'css:User-Agent',
       'css:browser', 'css:env-1-height', 'css:env-1-width',
       'css:env-10-height', 'css:env-10-width', 'css:env-11-height',
       'css:env-11-width', 'css:env-12-height', 'css:env-12-width',
       'css:env-13-height', 'css:env-13-width', 'css:env-14-height',
       'css:env-14-width', 'css:env-2-height', 'css:env-2-width',
       'css:env-3-height', 'css:env-3-width', 'css:env-5-height',
       'css:env-5-width', 'css:env-6-height', 'css:env-6-width',
       'css:env-7-height', 'css:env-7-width', 'css:env-8-height',
       'css:env-8-width', 'css:env-9-height', 'css:env-9-width',
       'css:image-set-heif', 'css:javascript', 'css:media-1-width',
       'css:media-10-width', 'css:media-2-width', 'css:media-3-width',
       'css:media-4-width', 'css:media-5-width', 'css:me